In [7]:
from datetime import date
import numpy as np
import pandas as pd

today = date.today()
d1 = today.strftime("%b-%d-%Y")

path_dependencies = '/Users/gd/GitHub/ECP/_code/compilation/_dependencies/dep_ecp'
exec(open(path_dependencies+'/pkgs_and_directories.py').read())
exec(open("/Users/gd/GitHub/WorldCarbonPricingDatabase/_code/_compilation/_dependencies/jurisdictions.py").read())

subnat_lists = {"United States":jurisdictions["subnationals"]["United States"], "Canada":jurisdictions["subnationals"]["Canada"], "China":jurisdictions["subnationals"]["China"]}
all_subnat_list = jurisdictions["subnationals"]["United States"]+jurisdictions["subnationals"]["Canada"]+jurisdictions["subnationals"]["China"]

gases = ["CO2"] # "CH4", "N2O", "FGASES" 


Loading data

In [2]:
wcpd = {}

# Load IPCC to IEA mapping once
ipcc_iea_map = pd.read_csv(
    "/Users/gd/GitHub/ECP/_raw/_aux_files/ipcc2006_iea_category_codes.csv",
    usecols=["ipcc_code", "FLOW"]
).rename(columns={"FLOW": "iea_code"})

for gas in gases:
    # Load WCPD data
    wcpd_ctry = ecp_general.concatenate(f"{path_wcpd}/{gas}/national")
    wcpd_subnat = ecp_general.concatenate(f"{path_wcpd}/{gas}/subnational")
    wcpd_all = pd.concat([wcpd_ctry, wcpd_subnat]).sort_values(by=["jurisdiction", "year"])

    # Clean and deduplicate
    wcpd_all["Product"] = wcpd_all["Product"].fillna('NA')
    wcpd_all = wcpd_all.drop_duplicates(subset=["jurisdiction", "year", "ipcc_code", "Product"])

    # Add IEA sector codes
    wcpd_all = wcpd_all.merge(ipcc_iea_map, on="ipcc_code", how="left")
    wcpd_all["iea_code"] = wcpd_all["iea_code"].fillna('NA')

    # Standardize jurisdiction names
    def standardize(names):
        return {name: name.replace(".", "").replace(",", "").replace(" ", "_") for name in names}

    ctry_names = wcpd_ctry["jurisdiction"].unique()
    subnat_names = wcpd_subnat["jurisdiction"].unique()
    countries_dic = standardize(ctry_names)
    subnat_dic = standardize(subnat_names)

    # Check for duplicates
    if wcpd_all.duplicated(["jurisdiction", "year", "ipcc_code", "Product"]).any():
        print(f"The dataset for {gas} contains duplicates!")

    # Add coverage factors
    wcpd_all = ecp_cov_fac.coverageFactors(wcpd_all, gas)

    # Handle mechanism overlaps
    overlap = pd.read_csv(f"/Users/gd/GitHub/WorldCarbonPricingDatabase/_raw/overlap/overlap_mechanisms_{gas}.csv")
    wcpd_all = ecp_overlap.overlap(wcpd_all, overlap)

    # Save
    wcpd[gas] = wcpd_all


/Users/gd/GitHub/ECP/_code/compilation/_dependencies/dep_ecp/ecp_v3_overlap.py:47: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  inst_df_ids.loc[:, "overlap_"+i[0]+"_"+i[1]] = 0
/Users/gd/GitHub/ECP/_code/compilation/_dependencies/dep_ecp/ecp_v3_overlap.py:48: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  inst_df_ids.loc[:, "overlap_"+i[0]+"_"+i[1]+"_ids"] = inst_df_ids.loc[:, scheme_columns[i[0]]] + inst_df_ids.loc[:, scheme_columns[i[1]]]
/Users/gd/GitHub/ECP/_code/compilation/_dependencies/dep_ecp/ecp_v3

In [8]:
priceSeriesPaths = {"cFlxRate":"/currentPrices/FlexXRate", 
                   "cFixRate":"/currentPrices/FixedXRate", 
                   "kFixRate":"/constantPrices/FixedXRate"}

price_cols = {"cFlxRate":["ets_price_usd", "tax_rate_incl_ex_usd"], 
              "cFixRate":["ets_price_usd", "tax_rate_incl_ex_usd"], 
              "kFixRate":["ets_price_usd_k", "tax_rate_incl_ex_usd_k"]}

ecp_cols = {"cFlxRate":["ecp_ets_usd", "ecp_tax_usd", "ecp_all_usd"],
            "cFixRate":["ecp_ets_usd", "ecp_tax_usd", "ecp_all_usd"],
            "kFixRate":["ecp_ets_usd_k", "ecp_tax_usd_k", "ecp_all_usd_k"]}

IPCC1AList = ["1A", "1B", "1C", 
              "1A1", "1A2", "1A3", "1A4", "1A5", 
              "1A1A", "1A1B", "1A1C", "1A2A", "1A2B", "1A2C",
              "1A2D", "1A2E", "1A2F", "1A2G", "1A2H", "1A2I", 
              "1A2J", "1A2K", "1A2L", "1A2M", 
              "1A3A", "1A3B", "1A3C", "1A3D", "1A3E",
              "1A4A", "1A4B", "1A4C", "1A5A", "1A5B", "1A5C",
              "1A1A1", "1A1A2", "1A1A3", "1A3A1", "1A3A2", "1A3D1", "1A3D2", "1A3E1",
              "1A4C1", "1A4C2", "1A4C3",
              "1A5A", "1A5B", "1A5C"]

# "1A1C" - excluding one of the two IPCC categories associated with IEA flow ABFLOW011

# specify which price series is being calculated
priceSeriesList =  ["cFlxRate", "kFixRate"]

# select jurisdiction level for which calculations are executed [for now, only 'national']
jurGroup = "national"

# list of IPCC categories for which aggregate prices have to be calculated
# for most categories, this would simply involve an aggregation from product to category level; 
# for aggregate categories, it implies an additional aggregation from subcategories
priceCat = {"level_5":["1A1A1", "1A1A2", "1A1A3", "1A3A1", "1A3A2", "1A3D1", 
                       "1A3D2", "1A3E1", "1A4C1", "1A4C2", "1A4C3"],
            "level_4":["1A1A", "1A1B", "1A1C", "1A2A", "1A2B", "1A2C",
                       "1A2D", "1A2E", "1A2F", "1A2G", "1A2H", 
                       "1A2I", "1A2J", "1A2K", "1A2L", "1A2M",
                       "1A3A", "1A3B", "1A3C", "1A3D", "1A4A", 
                       "1A4B", "1A4C", "1A5A", "1A5B", "1A5C",
                       "1B2A", "1B2B",
                       "3C1A", "3C1B", "3C1C", "3C1D"], 
             "level_3":["1A2", "1A5", "1B1", 
                        "2A1", "2A2", "2A3", "2A4", "2H1", "2H2",
                        "3A1", "3A2", 
                        "3B1", "3B2", "3B3", "3B4", "3B5", "3B6",
                        "3C1", "3C2", "3C3", "3C4", "3C5", "3C6", "3C7", "3C8"],
             "level_2":["2A", "2B", "2C", "2D", "2E", "2F", "2G", 
                        "4A", "4B", "4C", "4D", "4E",
                        "5A", "5B"]
}

# list of IPCC categories that are aggregate of lower level categories in the inventory structure
aggCatList = ["1", "1A", "1A1A", "1A2", "1A3",
              "1A3A", "1A3D", "1A3E", "1A4", "1A4C",
              "1A5", "1B", "1B1", "1B1A", "1B1A1",
              "1B1A2", "1B2", "1B2A", "1B2A3", "1B2B",
              "1B2B3", "1C", "1C1", "1C2", "2",
              "2A", "2A4", "2B", "2B8", "2B9", "2C",
              "2D", "2E", "2F", "2G", "2H", "3", 
              "3A", "3B", "3B1", "3B2", "3B3", "3B4",
              "3B5", "3B6", "3B6B", "3C", "3D", "4",
              "4A", "4C", "4D", "5", "5A"]

IPCC1AListSubCat = list(set(IPCC1AList)-set(aggCatList))

In [ ]:
dfSecPrice = {}

for gas in ["CO2"]:  # extend for multiple gases if needed
    for priceSeries in priceSeriesList:

        results = []  # accumulate DataFrames here instead of repeated concat
        priceSeriesPath = priceSeriesPaths[priceSeries]

        # 1. Load initial sector-level prices
        cfWeightedP = ecp_sec_em.cfWeightedPrices(
            gas, priceSeries, priceSeriesPath,
            price_cols, wcpd[gas], countries_dic, subnat_dic
        )
        cfWprices_usd, all_inst_col = cfWeightedP

        for level, categories in priceCat.items():
            for category in categories:

                # 2. Get inventory shares & merge
                inventoryShare = ecp_sec_em.inventoryShare(category, jurGroup, gas, level)
                merge_keys = ["jurisdiction", "year", "ipcc_code", "iea_code"]
                if category in IPCC1AListSubCat and jurGroup == "national":
                    merge_keys.append("Product")

                temp = inventoryShare.merge(cfWprices_usd, on=merge_keys, how="left")

                # 3. Fill missing shares using helper
                def fill_default_weights(temp, category):
                    share_col = f"{gas}_shareAggSec"
                    if category in IPCC1AListSubCat and jurGroup == "national":
                        total_CO2 = temp.groupby(["jurisdiction", "year"])["CO2"].transform("sum")
                        temp.loc[temp[share_col].isna() & (total_CO2 == 0), share_col] = 1/3
                        temp.loc[temp[share_col].isna() & (total_CO2 != 0), share_col] = 0
                    else:
                        subCatcodes = [c for c in temp.ipcc_code.unique() 
                                       if c.startswith(category) and len(c) == len(category) + 1]
                        weight = 1 / len(subCatcodes) if subCatcodes else 1
                        cond = temp.ipcc_code.isin(subCatcodes) if subCatcodes else temp.ipcc_code == category
                        temp.loc[cond & temp[share_col].isna(), share_col] = weight
                    return temp

                temp = fill_default_weights(temp, category)

                # 4. Compute weighted price
                temp = temp.fillna({price_cols[priceSeries][0]: 0, price_cols[priceSeries][1]: 0})
                temp = temp.assign(
                    **{
                        ecp_cols[priceSeries][0]: temp[price_cols[priceSeries][0]] * temp[f"{gas}_shareAggSec"],
                        ecp_cols[priceSeries][1]: temp[price_cols[priceSeries][1]] * temp[f"{gas}_shareAggSec"]
                    }
                )
                temp[ecp_cols[priceSeries][2]] = temp[ecp_cols[priceSeries][0]] + temp[ecp_cols[priceSeries][1]]

                temp.drop(columns=[all_inst_col] + price_cols[priceSeries], inplace=True)

                # 5. Aggregate
                if level == "level_5":
                    group_cols = ["jurisdiction", "year", "ipcc_code"]
                else:
                    temp = temp[temp.ipcc_code != category] if temp.ipcc_code.nunique() > 1 else temp
                    group_cols = ["jurisdiction", "year"]

                temp_sum = temp.groupby(group_cols).sum().reset_index()
                if level != "level_5":
                    temp_sum["ipcc_code"] = category

                results.append(temp_sum)

                # 6. If aggregate category, update cfWprices_usd for next loop iteration
                if category in aggCatList:
                    cfWprices_usd = cfWprices_usd[cfWprices_usd.ipcc_code != category]
                    cols = ["jurisdiction", "year", "ipcc_code"] + ecp_cols[priceSeries]
                    temp_agg = temp_sum[cols].assign(Product=np.nan)
                    colMap = dict(zip(ecp_cols[priceSeries], price_cols[priceSeries] + [all_inst_col]))
                    cfWprices_usd = pd.concat([cfWprices_usd, temp_agg.rename(columns=colMap)])

        # 7. Finalize
        df_final[["ecp_ets_usd_k", "ecp_tax_usd_k", "ecp_all_usd_k"]] = df_final[["ecp_ets_usd_k", "ecp_tax_usd_k", "ecp_all_usd_k"]] / df_final[["CO2_shareAggSec"]]

        df_final = pd.concat(results).sort_values(["jurisdiction", "year", "ipcc_code"]).fillna("NA")
        df_final.to_csv(
            f"/Users/gd/GitHub/ECP/_dataset/ecp/ipcc/ecp_ipcc/{priceSeriesPath}/ecp_ipcc_{gas}_{priceSeries}_{d1}.csv",
            index=False
        )

        dfSecPrice[gas] = df_final


In [ ]:
test = df_final[["ecp_ets_usd_k", "ecp_tax_usd_k", "ecp_all_usd_k"]].div(df_final["CO2_shareAggSec"])


Constant (year of introduction), jurisdiction-specific, weights

**Categories 1A (combustion) only**

In [9]:

# sector-level, recording year prior to first year of pricing mechanism implementation

firstYear = wcpd_all[['jurisdiction', 'year', 'ipcc_code', 'iea_code', 'Product', 'tax', 'ets']]

firstYear.loc[:, "pricing"] = firstYear.loc[:, "tax"] + firstYear.loc[:, "ets"]
firstYear.loc[:, "pricing"] = np.where(firstYear.loc[:, "pricing"] > 0, 1.0,0.0)
firstYear = firstYear.drop(["tax", "ets"], axis=1)
firstYear = firstYear.loc[firstYear.pricing == 1,]
firstYear.sort_values(by=["jurisdiction", "year", "ipcc_code", "Product"], ascending=True, inplace=True)

firstYear.drop_duplicates(subset=["jurisdiction", "ipcc_code", "Product"], inplace=True)

firstYear_cat = firstYear.groupby(["jurisdiction", "year", "ipcc_code", "iea_code"]).sum()
firstYear_cat.loc[:, "pricing"] = np.where(firstYear_cat.loc[:, "pricing"] > 0, 1.0, 0.0)
firstYear_cat.reset_index(inplace=True)
firstYear_cat = firstYear_cat.drop_duplicates(subset=["jurisdiction", "iea_code"]) #"IPCC_cat_code" - has to be sorted based on IEA_CODE because there are two IPCC catefories corresponding to IEA ABFLOW011
firstYear_cat.loc[:, "year"] = firstYear_cat.loc[:, "year"]-1 # to take the year before first year of implementation
firstYear_cat = firstYear_cat.drop("pricing", axis=1)

# same adjustment
firstYear_cat.loc[(firstYear_cat.jurisdiction=="Finland") & (firstYear_cat.year==1989), "year"] = 1990
firstYear_cat.loc[(firstYear_cat.jurisdiction=="Poland") & (firstYear_cat.year==1989), "year"] = 1990

/var/folders/hs/0dcrvt2s3gj57xgyfxrq3ft80000gn/T/ipykernel_58490/325700244.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  firstYear.loc[:, "pricing"] = firstYear.loc[:, "tax"] + firstYear.loc[:, "ets"]
/var/folders/hs/0dcrvt2s3gj57xgyfxrq3ft80000gn/T/ipykernel_58490/325700244.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  firstYear.loc[:, "pricing"] = np.where(firstYear.loc[:, "pricing"] > 0, 1.0,0.0)


In [10]:
# Note: currently, for this function to run, `priceSeries` must be set to "kFixRate" above
inventoryPath = "/Users/gd/OneDrive - rff/Documents/Research/projects/ecp/ecp_dataset/source_data/ghg_inventory/processed/"
invName = {"national":"nat", "subnational":"subnat"}
inventory = pd.read_csv(inventoryPath+"/inventory_"+invName[jurGroup]+"_"+gas+".csv")

inventory = inventory[['jurisdiction', 'year', 'ipcc_code', 'iea_code', 'Product', gas]]
inventory = inventory.loc[inventory.year<=2018, :]

for yr in range(2019, 2023):
    temp = inventory.loc[inventory.year==2018, :].copy()
    temp["year"].replace(to_replace={2018:yr}, inplace=True)

    inventory = pd.concat([inventory, temp])

inventory = inventory.loc[~inventory.iea_code.isnull()]

aggSecEm = inventory.groupby(["jurisdiction", "year", 'ipcc_code', 'iea_code']).sum()
aggSecEm.reset_index(inplace=True)

share_df = inventory.merge(aggSecEm[["jurisdiction", "year", "iea_code", gas]], 
                                            on=["jurisdiction", "year", "iea_code"], how='left')
share_df[gas+"_shareAggSec"] = share_df[gas+"_x"]/share_df[gas+"_y"]

share_df.drop(["CO2_y"], axis=1, inplace=True)
share_df.rename(columns={gas+"_x":gas}, inplace=True)



In [23]:

def ecp_constIntroCat(share_df, prices):

    df_concat = pd.DataFrame()

    for jur in share_df.jurisdiction.unique():
        # sectors for which a price is in place at one point in the sample
        sectors = firstYear_cat.loc[(firstYear_cat.jurisdiction==jur), :]["iea_code"].unique()

        for sector in share_df.loc[share_df.jurisdiction==jur, "iea_code"].unique():
            if jur in firstYear_cat.jurisdiction.unique() and sector in sectors:
                weight_year = firstYear_cat.loc[(firstYear_cat.jurisdiction==jur) & (firstYear_cat.iea_code==sector)]["year"].item()
            else:
                weight_year = 2015

            temp_df = share_df[(share_df["jurisdiction"]==jur) & (share_df["year"]==weight_year) & (share_df["iea_code"]==sector)]
            temp_df.drop("year", axis=1, inplace=True)

            merge_keys = ["jurisdiction", "ipcc_code", "iea_code", "Product"]
            temp_df = temp_df.merge(prices, on=merge_keys, how="left")

            temp_df[["ets_price_usd_k", "tax_rate_incl_ex_usd_k"]].fillna(0, inplace=True)

            temp_df["ecp_ets_ew_usd_k"] = (temp_df.ets_price_usd_k)*temp_df.CO2_shareAggSec
            temp_df["ecp_tax_ew_usd_k"] = (temp_df.tax_rate_incl_ex_usd_k)*temp_df.CO2_shareAggSec
            temp_df["ecp_all_ew_usd_k"] = (temp_df.ets_price_usd_k.fillna(0) + temp_df.tax_rate_incl_ex_usd_k.fillna(0))*temp_df.CO2_shareAggSec

            temp_df.drop(["ets_price_usd_k", "tax_rate_incl_ex_usd_k", "all_inst_usd_k"], axis=1, inplace=True)

            temp_df_sum = temp_df.groupby(["jurisdiction", "year", "iea_code"]).sum()
            temp_df_sum.reset_index(inplace=True)

            temp_df_sum = temp_df_sum[["jurisdiction", "year", "iea_code", 
                                        "ecp_ets_ew_usd_k", "ecp_tax_ew_usd_k", "ecp_all_ew_usd_k"]]

            if df_concat.empty == True:
                df_concat = temp_df_sum
            else:
                df_concat = pd.concat([df_concat, temp_df_sum])
        
    return df_concat


In [24]:
ecp_ipcc_intro = ecp_constIntroCat(share_df, cfWprices_usd)


/var/folders/hs/0dcrvt2s3gj57xgyfxrq3ft80000gn/T/ipykernel_58490/4155320593.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  temp_df.drop("year", axis=1, inplace=True)
/var/folders/hs/0dcrvt2s3gj57xgyfxrq3ft80000gn/T/ipykernel_58490/4155320593.py:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  temp_df[["ets_price_usd_k", "tax_rate_incl_ex_usd_k"]].fillna(0, inplace=True)
/var/folders/hs/0dcrvt2s3gj57xgyfxrq3ft80000gn/T/ipykernel_58490/4155320593.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-

In [25]:
ecp_ipcc_intro.to_csv("/Users/gd/OneDrive - rff/Documents/Research/projects/ecp/ecp_dataset/data/ecp/ecp_ipcc/ecp_intro/ecp_ipcc_CO2_intro.csv", index=None)